In [1]:
!pip install sentence_transformers
!pip install nltk
!pip install datefinder
!pip install dateparser
import json
from tqdm import tqdm
from sentence_transformers import CrossEncoder
import nltk
nltk.download('punkt')
from nltk.tokenize import sent_tokenize

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 227.1/227.1 kB 3.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 295.0/295.0 kB 6.6 MB/s eta 0:00:00


/opt/conda/lib/python3.10/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:11: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange
2024-06-09 17:14:06.964422: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-06-09 17:14:06.964563: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-06-09 17:14:07.081314: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


[nltk_data] Downloading package punkt to /usr/share/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [2]:
import torch

with open(r'/kaggle/input/claim-decomp-data/nli_input_val_evidence_withoutrerank.json', 'r') as f:
    snippets = json.load(f)

with open(r'/kaggle/input/quantemp-evidence-snippets/nli_input_val_reranktop5.json', 'r') as f:
    base_top5_evidence = json.load(f)
    
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(f"Using device: {device}")

Using device: cuda


In [3]:
import datefinder
import dateparser
from dateparser import DateDataParser

import re

def strip_non_digits(text):
    # Use regex to find the first sequence of digits
    match = re.search(r'\d.*\d', text)
    
    # If a match is found, return the matched part
    if match:
        return match.group(0)
    
    # If no match is found, return an empty string
    return ''

ddp = DateDataParser(settings={'PARSERS':['absolute-time'],'PREFER_DATES_FROM': 'past', 'REQUIRE_PARTS': ['year']})

def extract_date(text):
    # use datefinder to first find potential dates - because dateparser isn't very good at it
    dates = datefinder.find_dates(text, source=True)
    for date, string in dates:
        
        # parse the date properly - because datefinder isn't very good at it
        parsed = ddp.get_date_data(string)['date_obj']
    
        # don't want 'dates' like '91.5 percent' to show up as 1991 / 5 
        try:
            if float(strip_non_digits(string)) < 1500:
                continue
        except ValueError:
            pass
        
        # return the first date as the timestamp
        if parsed is not None:
            return parsed

    return None
        


print(dateparser.parse("of 50", date_formats=['%y'], settings={'PARSERS':['custom-formats']}))

# Example usage
text = "A total of 58 peer-reviewed papers published in the first half of 2017 conclude that global warming is a myth."

print(extract_date(text))

None
2017-06-09 00:00:00


In [4]:
import numpy as np

re_ranker = CrossEncoder('cross-encoder/ms-marco-MiniLM-L-6-v2')
re_ranker.model.to(device)


# scaling factor of temporal score w.r.t semantic score
ALPHA = 0.5

def get_temporal_score(snippet, query_timestamp, alpha=ALPHA):
    doc_date = extract_date(snippet)
    if doc_date is None:
        return None
    
    dt = doc_date.timestamp()
    score = alpha / (query_timestamp - dt + 0.1)
    return score
    
    

def temporal_rerank(claim, evidence_list, top_k=5):
    claim_date = extract_date(claim)
    
    if claim_date is None:
        return None
        
    claim_date = claim_date.timestamp()
    
    pairs = [[claim, snippet] for snippet in evidence_list if snippet.strip()]  # Remove empty or whitespace-only snippets
    
    semantic_scores = re_ranker.predict(pairs)
    temp_scores = np.array([get_temporal_score(snippet, claim_date) for snippet in evidence_list])
    
    u_s = np.mean(semantic_scores)
    u_t = np.mean(temp_scores[temp_scores != np.array(None)])

    o_s = np.std(semantic_scores)
    o_t = np.std(temp_scores[temp_scores != np.array(None)])
    
    for i, snippet in enumerate(evidence_list):
        if temp_scores[i] == None:
            continue
        elif temp_scores[i] < 0:
            semantic_scores[i] = - float("inf")
        else:
            semantic_scores[i] += (temp_scores[i] - u_t) / o_t * o_s + u_s
        
    ranked_snippets = [snippet for _, snippet in sorted(zip(semantic_scores, evidence_list), reverse=True)]
    return ' '.join(ranked_snippets[:top_k]) 


/opt/conda/lib/python3.10/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


config.json:   0%|          | 0.00/794 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/90.9M [00:00<?, ?B/s]

/opt/conda/lib/python3.10/site-packages/torch/_utils.py:831: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  return self.fget.__get__(instance, owner)()


tokenizer_config.json:   0%|          | 0.00/316 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

In [5]:
temporal_evidence = []

for snippet, top5 in tqdm(list(zip(snippets, base_top5_evidence))):
    reranked_evidence = temporal_rerank(snippet['claim'], snippet['evidence_snippet_list'])

    if reranked_evidence is None:
        nli_input = {
            'claim': snippet['claim'],
            'evidence': top5['evidence'],
            'extracted_date': None
        }
    else:
        nli_input = {
            'claim': snippet['claim'],
            'evidence': reranked_evidence,
            'extracted_date': str(extract_date(snippet['claim']))
        }
    temporal_evidence.append(nli_input)

  0%|          | 1/3084 [00:00<10:51,  4.73it/s]

Batches:   0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 8/3084 [00:05<38:58,  1.32it/s]

Batches:   0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 9/3084 [00:07<49:20,  1.04it/s]

...

100%|█████████▉| 3078/3084 [17:50<00:01,  3.80it/s]

Batches:   0%|          | 0/4 [00:00<?, ?it/s]

100%|█████████▉| 3083/3084 [17:52<00:00,  3.90it/s]

Batches:   0%|          | 0/4 [00:00<?, ?it/s]

100%|██████████| 3084/3084 [17:53<00:00,  2.87it/s]


In [6]:
with open('/kaggle/working/nli_input_val_reranktop5_temporal.json', 'w') as f:
    json.dump(temporal_evidence, f)